### Práctica de Acceso a bases de datos

Considerar una base de datos sobre diferentes índices bursatiles formada por las siguientes tablas:

__Tabla "Datos generales"__:

* Ticker (Valor único) Cadena	
* Nombre Cadena	
* Índice Cadena	
* País Cadena		

__Tabla "IBEX35"__:

* TKR (Valor único y hace referencia al campo Ticker de la tabla Datos generales)  Cadena	
* Precio Decimal
* Var.(%) Decimal
* Var.(€) Decimal
* Máx. Decimal
* Mín. Decimal
* Volumen Entero

__Tabla "DAX30"__:

* TKR (Valor único y hace referencia al campo Ticker de la tabla Datos generales)  Cadena	
* Precio Decimal
* Var.(%) Decimal
* Var.(€) Decimal
* Máx. Decimal
* Mín. Decimal
* Volumen Entero

__Tabla "NASDAQ100"__:

* TKR (Valor único y hace referencia al campo Ticker de la tabla Datos generales)  Cadena	
* Precio Decimal
* Var.(%) Decimal
* Var.(€) Decimal
* Máx. Decimal
* Mín. Decimal
* Volumen Entero

__Tabla "FTSE_MIB"__:

* TKR (Valor único y hace referencia al campo Ticker de la tabla Datos generales)  Cadena	
* Precio Decimal
* Var.(%) Decimal
* Var.(€) Decimal
* Máx. Decimal
* Mín. Decimal
* Volumen Entero

__Tabla "SemanalesIBEX35"__:

* Ticker (Valor único y hace referencia al campo Ticker de la tabla Datos generales)  Cadena	
* Fecha Cadena
* Price Decimal
* Low Decimal
* High Decimal

Los datos de las tablas se encuentran en los archivos csv "Tabla1.csv", "Tabla2(IBEX35).csv", "Tabla3(DAX30).csv", "Tabla4(Nasdaq 100).csv", "Tabla5(Ftse Mib).csv" y "Tabla6(SemanalesIBEX35).csv".La tabla 1 contiene datos identificativos de cada acción, las tablas 2-5 son los resultados de la cotización el día 5 de octubre de 2022, y la tabla 6 son datos históricos de las acciones del IBEX35.

Se pide:
1.  Hacer una función que cree la base de datos "Bolsa" con sus tablas y datos correspondientes. Para ello habrá que procesar los archivos csv proporcionados.Tomar las decisiones necesarias para relacionar adecuadamente las tablas, así como restricciones en cuanto a unicidad o tipos de datos. Igualmente procesad adecuadamente el campo fecha de la tabla "SemanalesIBEX35"para poder utilizarlo en las consultas(3 puntos).

2.  Resolver las siguientes consultas(7 puntos):

* Considerar la máxima diferencia entre el valor máximo y el valor mínimo de las acciones de todos los índices. Mostrar el nombre de la/s acción/es cuya diferencia alcanza ese valor, el nombre del indice al que pertenece y el valor de la diferencia tomada

* Obtener la suma de los volumenes negociados agregados por el índice al que pertenecen y ordenados de mayor a menor. Se mostrará el nombre del índice, el país al que pertenece y la suma de los volúmenes del índice.

* Obtener aquellas acciones cuyo variación entre el máximo y el mínimo en la jornada del 5 de octubre fue menor que la variacion entre el valor low y high en la serie histórica. Mostrar el nombre de la acción y las diferencias.

* Obtener la media de los valores de las acciones de la serie histórica del IBEX35 ordenadas decrecientemente por la media de los valores.

* Obtener la acción que más valió y más volumen de titulos negoció en la jornada del 5 de octubre. Mostrar el nombre de la acción, el índice al que pertenece y el pais.

* Obtener las diferencias de precio entre cada par de acciones en la serie histórica del IBEX35 por fecha. Mostrar el nombre de las accciones, la fecha y la diferencia de valor ordenadas decrecientemente por la fecha.

* ¿En que fecha de la serie histórica del IBEX35 hubo más acciones donde la diferencia entre el valor maximo y el precio final fue 0?
  Mostrar los nombres de las acciones y la fecha.
  
#### Normas de entrega

* Fecha tope de entrega: 13/10/2022
* La entrega se realizará subiendo al campus virtual un notebook de Jupyter con la solución. El archivo tendrá como nombre BasesDatos_GrupoX donde X será el número de grupo correspondiente.


In [1]:
import sqlite3
import csv
from datetime import datetime

#Ejercicio 1:

#Crear las tablas
def crearTablas(cur):
    cur.execute("DROP TABLE IF EXISTS IBEX35")
    cur.execute("DROP TABLE IF EXISTS DAX30")
    cur.execute("DROP TABLE IF EXISTS NASDAQ100")
    cur.execute("DROP TABLE IF EXISTS FTSE_MIB")
    cur.execute("DROP TABLE IF EXISTS SemanalesIBEX35")
    cur.execute("DROP TABLE IF EXISTS DatosGenerales")
    cur.execute("CREATE TABLE DatosGenerales(Ticker TEXT PRIMARY KEY, Nombre TEXT NOT NULL, Indice TEXT NOT NULL, Pais TEXT NOT NULL)")
    cur.execute("CREATE TABLE IBEX35(TKR TEXT UNIQUE, Precio FLOAT(2) NOT NULL, 'Var.(%)' FLOAT(2) NOT NULL, 'Var.(€)' FLOAT(2) NOT NULL, Max FLOAT(2) NOT NULL, Min FLOAT(2) NOT NULL, Volumen INTEGER NOT NULL, FOREIGN KEY(TKR) REFERENCES DatosGenerales(Ticker))")
    cur.execute("CREATE TABLE DAX30(TKR TEXT UNIQUE, Precio FLOAT(2) NOT NULL, 'Var.(%)' FLOAT(2) NOT NULL, 'Var.(€)' FLOAT(2) NOT NULL, Max FLOAT(2) NOT NULL, Min FLOAT(2) NOT NULL, Volumen INTEGER NOT NULL, FOREIGN KEY(TKR) REFERENCES DatosGenerales(Ticker))")
    cur.execute("CREATE TABLE NASDAQ100(TKR TEXT UNIQUE, Precio FLOAT(2) NOT NULL, 'Var.(%)' FLOAT(2) NOT NULL, 'Var.(€)' FLOAT(2) NOT NULL, Max FLOAT(2) NOT NULL, Min FLOAT(2) NOT NULL, Volumen INTEGER NOT NULL, FOREIGN KEY(TKR) REFERENCES DatosGenerales(Ticker))")
    cur.execute("CREATE TABLE FTSE_MIB(TKR TEXT UNIQUE, Precio FLOAT(2) NOT NULL, 'Var.(%)' FLOAT(2) NOT NULL, 'Var.(€)' FLOAT(2) NOT NULL, Max FLOAT(2) NOT NULL, Min FLOAT(2) NOT NULL, Volumen INTEGER NOT NULL, FOREIGN KEY(TKR) REFERENCES DatosGenerales(Ticker))")
    cur.execute("CREATE TABLE SemanalesIBEX35(ID INTEGER PRIMARY KEY, Ticker TEXT, Fecha TEXT NOT NULL, Price FLOAT(2) NOT NULL, Low FLOAT(2) NOT NULL, High FLOAT(2) NOT NULL, FOREIGN KEY(Ticker) REFERENCES DatosGenerales(Ticker))")

#Leer datos del CSV
def leerCSV(nombre):
    csvarchivo = open(nombre,encoding="utf8",errors='ignore')
    return csv.reader(csvarchivo, delimiter=";")

#Insertar datos en la BD
def insertarDatos(cur):
    #Datos de la Tabla Datos Generales
    lista = leerCSV("Tabla1.csv")
    for i in lista:
        if(lista.line_num == 1):
            continue
        cur.execute("INSERT INTO DatosGenerales (Ticker, Nombre, Indice, Pais) VALUES (?, ?, ?, ?)", (i[0], i[1], i[2], i[3]))
    
    #Datos para Tabla 2 - 5
    nombre = "Tabla2(IBEX35).csv"
    tabla = "IBEX35"
    j = 0
    while (j < 4):
        lista = leerCSV(nombre)
        for i in lista:
            if(lista.line_num == 1):
                continue
            cur.execute("INSERT INTO " + tabla + "(TKR, Precio, 'Var.(%)', 'Var.(€)', Max, Min, Volumen) VALUES (?, ?, ?, ?, ?, ?, ?)", (i[0], i[1], i[2], i[3], i[4], i[5], i[6]))
        j += 1
        if(j == 1):
            nombre = "Tabla3(DAX 30).csv"
            tabla = "DAX30"
        elif(j == 2):
            nombre = "Tabla4(Nasdaq 100).csv"
            tabla = "NASDAQ100"
        else:
            nombre = "Tabla5(Ftse Mib).csv"
            tabla = "FTSE_MIB"
            
    #Datos para la Tabla SemanalesIBEX35
    lista = leerCSV("Tabla6(SemanalesIBEX35).csv")
    for i in lista:
        if(lista.line_num == 1):
            continue
        fecha = i[1][6:10] + "-" + i[1][3:5] + "-" + i[1][0:2]
        cur.execute("INSERT INTO SemanalesIBEX35 (Ticker, Fecha, Price, Low, High) VALUES (?, ?, ?, ?, ?)", (i[0], (datetime.strptime(fecha, "%Y-%m-%d")).strftime("%Y-%m-%d"), float(i[2].replace(',','.')),float(i[3].replace(',','.')),float(i[4].replace(',','.'))))

        
conn=sqlite3.connect("Bolsa.sqlite3")
conn.execute("PRAGMA foreign_keys = 1")
cur=conn.cursor()

#Crear las tablas y procesar informacion 
crearTablas(cur)
insertarDatos(cur)

cur.close()
conn.commit()

In [2]:
#Mostrar la consulta
def mostrar(cur):
    while True:
        fila=cur.fetchone()
        if not fila: break
        print (fila)   

In [3]:
import sqlite3

conn=sqlite3.connect("Bolsa.sqlite3")
conn.execute("PRAGMA foreign_keys = 1")
cur=conn.cursor()

#Consulta 1:
#Considerar la máxima diferencia entre el valor máximo y el valor mínimo de las acciones de todos los índices.
#Mostrar el nombre de la/s acción/es cuya diferencia alcanza ese valor, el nombre del indice al que pertenece 
#y el valor de la diferencia tomada
cur.execute(
"SELECT Nombre," +
"       Indice," +
"       MAX(dif)" + 
"  FROM ( " +
"           SELECT G.Nombre," +
"                  G.Indice," +
"                  MAX(N.Max - N.Min) AS dif" +
"             FROM DatosGenerales G" +
"                  LEFT JOIN" +
"                  NASDAQ100 N ON G.Ticker = N.TKR" +
"           UNION ALL" +
"           SELECT G.Nombre," +
"                  G.Indice," +
"                  MAX(D.Max - D.Min) AS dif" +
"             FROM DatosGenerales G" +
"                  LEFT JOIN" +
"                  DAX30 D ON G.Ticker = D.TKR" +
"           UNION ALL" +
"           SELECT G.Nombre," +
"                  G.Indice," +
"                  MAX(F.Max - F.Min) AS dif" +
"             FROM DatosGenerales G" +
"                  LEFT JOIN" +
"                  FTSE_MIB F ON G.Ticker = F.TKR" +
"           UNION ALL" +
"           SELECT G.Nombre," +
"                  G.Indice," +
"                  MAX(I.Max - I.Min) AS dif" +
"             FROM DatosGenerales G" +
"                  LEFT JOIN" +
"                  IBEX35 I ON G.Ticker = I.TKR)"
)


mostrar(cur)

cur.close()
conn.commit()

('INTUIT INC', 'Nasdaq 100', 412.65)


In [4]:
import sqlite3

conn=sqlite3.connect("Bolsa.sqlite3")
conn.execute("PRAGMA foreign_keys = 1")
cur=conn.cursor()

#Consulta 2:
#Obtener la suma de los volumenes negociados agregados por el índice al que pertenecen y ordenados de mayor a menor.
#Se mostrará el nombre del índice, el país al que pertenece y la suma de los volúmenes del índice 
cur.execute(
"SELECT Indice," +
"       Pais," +
"       SUM(Volumen) " +
"  FROM DatosGenerales" +
"       LEFT JOIN" +
"       DAX30 ON DatosGenerales.Ticker = DAX30.TKR " +
"UNION " +
"SELECT Indice," +
"       Pais," +
"       SUM(Volumen) " +
"  FROM DatosGenerales" +
"       JOIN" +
"       FTSE_MIB ON DatosGenerales.Ticker = FTSE_MIB.TKR " +
"UNION " +
"SELECT Indice," +
"       Pais," +
"       SUM(Volumen) " +
"  FROM DatosGenerales" +
"       JOIN" +
"       IBEX35 ON DatosGenerales.Ticker = IBEX35.TKR " +
"UNION " +
"SELECT Indice," +
"       Pais," +
"       SUM(Volumen) " +
"  FROM DatosGenerales" +
"       JOIN" +
"       NASDAQ100 ON DatosGenerales.Ticker = NASDAQ100.TKR" +
" ORDER BY sum(Volumen) DESC;"
)

mostrar(cur)

cur.close()
conn.commit()

('Nasdaq 100', 'USA', 842896255)
('Ftse Mib', 'Italia', 395854403)
('IBEX 35', 'Espaa', 130259371)
('DAX 30', 'Alemania', 56194717)


In [5]:
import sqlite3

conn=sqlite3.connect("Bolsa.sqlite3")
conn.execute("PRAGMA foreign_keys = 1")
cur=conn.cursor()

#Consulta 3:
#Obtener aquellas acciones cuyo variación entre el máximo y el mínimo en la jornada del 5 de octubre 
#fue menor que la variacion entre el valor low y high en la serie histórica.
#Mostrar el nombre de la acción y las diferencias.
cur.execute(
"SELECT G.Nombre," +
"       ( (S.High - S.Low) - (I.Max - I.Min) ) AS Diferencia" +
"  FROM DatosGenerales G" +
"       JOIN" +
"       IBEX35 I ON G.Ticker = I.TKR" +
"       JOIN" +
"       SemanalesIBEX35 S ON G.Ticker = S.Ticker" +
" WHERE (I.Max - I.Min) < (S.High - S.Low);"
)

mostrar(cur)

cur.close()
conn.commit()

('ACS', 0.240000000000002)
('ACERINOX SA', 0.6499999999999986)
('AENA', 1.1999999999999886)
('AMADEUS', 2.1000000000000014)
('ACCIONA', 9.200000000000017)
('CRP ACC ENER RN BR', 1.8900000000000041)
('BANCO DE BILBAO VIZCAYA', 0.29000000000000004)
('BANKINTER', 0.11999999999999922)
('CAIXABANK', 0.07999999999999963)
('CELLNEX TELECOM', 1.5200000000000031)
('ENDESA', 0.8599999999999994)
('ENAGAS', 0.1499999999999968)
('FLUIDRA', 1.9100000000000001)
('FERROVIAL', 0.9499999999999993)
('GRIFOLS CL.A', 0.6799999999999962)
('IAG GROUP', 0.13000000000000056)
('IBERDROLA', 0.4399999999999995)
('INDRA SISTEMAS', 0.5700000000000003)
('INDITEX', 0.6799999999999997)
('MAPFRE', 0.03000000000000025)
('MELIA HOTELS', 0.1999999999999993)
('MERLIN PROPERTIES', 0.09000000000000075)
('ARCELORMITTAL', 2.0199999999999996)
('NATURGY ENERGY', 2.9299999999999997)
('PHARMA MAR', 0.7199999999999847)
('RED ELECTRICA', 0.12999999999999723)
('REPSOL', 0.3200000000000003)
('LABORATORIOS FARMACEUTICOS ROV', 3.1800000

In [6]:
import sqlite3

conn=sqlite3.connect("Bolsa.sqlite3")
conn.execute("PRAGMA foreign_keys = 1")
cur=conn.cursor()

#Consulta 4:
#Obtener la media de los valores de las acciones de la serie histórica del IBEX35 ordenadas 
#decrecientemente por la media de los valores.
cur.execute(
"SELECT AVG(Price)" +
" FROM SemanalesIBEX35" +
"  GROUP BY Ticker" +
"  ORDER BY AVG(Price) desc")

mostrar(cur)

cur.close()
conn.commit()

(173.75098039215692,)
(135.57058823529408,)
(62.54470588235293,)
(60.5770588235294,)
(56.90039215686273,)
(43.47176470588235,)
(34.240980392156864,)
(26.57078431372548,)
(26.38568627450981,)
(25.349803921568625,)
(25.210588235294114,)
(24.468823529411758,)
(23.245294117647067,)
(19.752352941176472,)
(18.98470588235294,)
(18.891568627450976,)
(18.31411764705883,)
(18.273137254901958,)
(16.16411764705882,)
(12.189803921568627,)
(10.316470588235296,)
(10.176470588235293,)
(9.79686274509804,)
(9.371372549019606,)
(7.3801960784313705,)
(6.403137254901958,)
(5.180588235294119,)
(5.037647058823527,)
(4.225098039215685,)
(2.9321568627450985,)
(2.87607843137255,)
(2.2923529411764707,)
(1.7723529411764711,)
(1.5943137254901956,)
(0.704705882352941,)


In [7]:
import sqlite3

conn=sqlite3.connect("Bolsa.sqlite3")
conn.execute("PRAGMA foreign_keys = 1")
cur=conn.cursor()

#Consulta 5:
#Obtener la acción que más valió y más volumen de titulos negoció en la jornada del 5 de octubre.
#Mostrar el nombre de la acción, el índice al que pertenece y el pais.
cur.execute(
"SELECT dag.Nombre," +
"       dag.Pais," +
"       dag.Indice" +
"  FROM (" +
"           SELECT TKR," +
"                  MAX(Volumen) " +
"             FROM (" +
"                      SELECT TKR," +
"                             Volumen" +
"                        FROM DAX30" +
"                      UNION " +
"                      SELECT TKR," +
"                             Volumen" +
"                        FROM FTSE_MIB" +
"                      UNION " +
"                      SELECT TKR," +
"                             Volumen" +
"                        FROM IBEX35" +
"                      UNION " +
"                      SELECT TKR," +
"                             Volumen" +
"                        FROM NASDAQ100" +
"                  ) " +
"       ) " +
"       sol " +
"       JOIN " +
"       DatosGenerales dag ON dag.Ticker == sol.TKR " +
"UNION " +
"SELECT dag.Nombre," +
"       dag.Pais," +
"       dag.Indice" +
"  FROM (" +
"           SELECT TKR," +
"                  MAX(Precio) " +
"             FROM (" +
"                      SELECT TKR," +
"                             Precio" +
"                        FROM DAX30" +
"                      UNION " +
"                      SELECT TKR," +
"                             Precio" +
"                        FROM FTSE_MIB" +
"                      UNION " +
"                      SELECT TKR," +
"                             Precio" +
"                        FROM IBEX35" +
"                      UNION " +
"                      SELECT TKR," +
"                             Precio" +
"                        FROM NASDAQ100" +
"                  ) " +
"       ) " +
"       sol " +
"       JOIN " +
"       DatosGenerales dag ON dag.Ticker == sol.TKR;"
)

mostrar(cur)

cur.close()
conn.commit()

('BOOKING HOLDINGS', 'USA', 'Nasdaq 100')
('INTESA SANPAOLO SPA', 'Italia', 'Ftse Mib')


In [8]:
import sqlite3

conn=sqlite3.connect("Bolsa.sqlite3")
conn.execute("PRAGMA foreign_keys = 1")
cur=conn.cursor()

#Consulta 6:
#Obtener las diferencias de precio entre cada par de acciones en la serie histórica del IBEX35 por fecha.
#Mostrar el nombre de las accciones, la fecha y la diferencia de valor ordenadas decrecientemente por la fecha.
cur.execute(
"SELECT G.Nombre," +
"       H.Nombre," +
"       S.Fecha," +
"       abs(S.Price - M.Price) AS DiferenciaPrecio" +
"  FROM SemanalesIBEX35 S," +
"       SemanalesIBEX35 M" +
"       JOIN" +
"       DatosGenerales G ON G.Ticker = S.Ticker" +
"       JOIN" +
"       DatosGenerales H ON H.Ticker = M.Ticker" +
" WHERE S.Fecha == M.Fecha AND " +
"       S.Ticker != M.Ticker" +
" ORDER BY S.Fecha DESC;"
)
mostrar(cur)

cur.close()
conn.commit()

('ACS', 'ACERINOX SA', '2022-09-30', 14.93)
('ACS', 'AENA', '2022-09-30', 83.77000000000001)
('ACS', 'AMADEUS', '2022-09-30', 24.779999999999998)
('ACS', 'ACCIONA', '2022-09-30', 157.47)
('ACS', 'CRP ACC ENER RN BR', '2022-09-30', 15.23)
('ACS', 'BANCO DE BILBAO VIZCAYA', '2022-09-30', 18.509999999999998)
('ACS', 'BANKINTER', '2022-09-30', 17.36)
('ACS', 'CAIXABANK', '2022-09-30', 19.82)
('ACS', 'CELLNEX TELECOM', '2022-09-30', 8.66)
('ACS', 'INMOBILIARIA COLONIAL', '2022-09-30', 18.189999999999998)
('ACS', 'ENDESA', '2022-09-30', 7.709999999999999)
('ACS', 'ENAGAS', '2022-09-30', 7.289999999999999)
('ACS', 'FLUIDRA', '2022-09-30', 7.609999999999999)
('ACS', 'FERROVIAL', '2022-09-30', 0.26000000000000156)
('ACS', 'GRIFOLS CL.A', '2022-09-30', 14.249999999999998)
('ACS', 'IAG GROUP', '2022-09-30', 22.049999999999997)
('ACS', 'IBERDROLA', '2022-09-30', 13.549999999999999)
('ACS', 'INDRA SISTEMAS', '2022-09-30', 15.27)
('ACS', 'INDITEX', '2022-09-30', 1.8499999999999979)
('ACS', 'MAPFRE',

('INDITEX', 'AMADEUS', '2022-09-23', 25.33)
('INDITEX', 'ACCIONA', '2022-09-23', 166.06)
('INDITEX', 'CRP ACC ENER RN BR', '2022-09-23', 18.340000000000003)
('INDITEX', 'BANCO DE BILBAO VIZCAYA', '2022-09-23', 16.28)
('INDITEX', 'BANKINTER', '2022-09-23', 15.07)
('INDITEX', 'CAIXABANK', '2022-09-23', 17.56)
('INDITEX', 'CELLNEX TELECOM', '2022-09-23', 10.810000000000002)
('INDITEX', 'INMOBILIARIA COLONIAL', '2022-09-23', 16.02)
('INDITEX', 'ENDESA', '2022-09-23', 4.09)
('INDITEX', 'ENAGAS', '2022-09-23', 4.140000000000001)
('INDITEX', 'FLUIDRA', '2022-09-23', 6.279999999999999)
('INDITEX', 'FERROVIAL', '2022-09-23', 2.2600000000000016)
('INDITEX', 'GRIFOLS CL.A', '2022-09-23', 11.01)
('INDITEX', 'IAG GROUP', '2022-09-23', 19.91)
('INDITEX', 'IBERDROLA', '2022-09-23', 10.85)
('INDITEX', 'INDRA SISTEMAS', '2022-09-23', 13.139999999999999)
('INDITEX', 'MAPFRE', '2022-09-23', 19.38)
('INDITEX', 'MELIA HOTELS', '2022-09-23', 16.08)
('INDITEX', 'MERLIN PROPERTIES', '2022-09-23', 13.11)
('IND

('TELEFONICA', 'MELIA HOTELS', '2022-09-16', 1.69)
('TELEFONICA', 'MERLIN PROPERTIES', '2022-09-16', 5.16)
('TELEFONICA', 'ARCELORMITTAL', '2022-09-16', 18.330000000000002)
('TELEFONICA', 'NATURGY ENERGY', '2022-09-16', 21.73)
('TELEFONICA', 'PHARMA MAR', '2022-09-16', 54.980000000000004)
('TELEFONICA', 'RED ELECTRICA', '2022-09-16', 13.84)
('TELEFONICA', 'REPSOL', '2022-09-16', 8.100000000000001)
('TELEFONICA', 'LABORATORIOS FARMACEUTICOS ROV', '2022-09-16', 41.8)
('TELEFONICA', 'BANCO DE SABADELL', '2022-09-16', 3.11)
('TELEFONICA', 'BANCO SANTANDER', '2022-09-16', 1.21)
('TELEFONICA', 'SACYR VALLEHERMOSO', '2022-09-16', 1.52)
('TELEFONICA', 'SIEMENS GAMESA', '2022-09-16', 14.11)
('TELEFONICA', 'SOLARIA ENERGIA Y MEDIO AMBIEN', '2022-09-16', 16.400000000000002)
('ACS', 'ACERINOX SA', '2022-09-09', 14.070000000000002)
('ACS', 'AENA', '2022-09-09', 97.14)
('ACS', 'AMADEUS', '2022-09-09', 29.149999999999995)
('ACS', 'ACCIONA', '2022-09-09', 176.69)
('ACS', 'CRP ACC ENER RN BR', '2022-09

('MAPFRE', 'AENA', '2022-09-02', 120.67999999999999)
('MAPFRE', 'AMADEUS', '2022-09-02', 49.97)
('MAPFRE', 'ACCIONA', '2022-09-02', 192.93)
('MAPFRE', 'CRP ACC ENER RN BR', '2022-09-02', 38.85)
('MAPFRE', 'BANCO DE BILBAO VIZCAYA', '2022-09-02', 2.8899999999999997)
('MAPFRE', 'BANKINTER', '2022-09-02', 3.3899999999999997)
('MAPFRE', 'CAIXABANK', '2022-09-02', 1.3599999999999999)
('MAPFRE', 'CELLNEX TELECOM', '2022-09-02', 36.699999999999996)
('MAPFRE', 'INMOBILIARIA COLONIAL', '2022-09-02', 4.24)
('MAPFRE', 'ENDESA', '2022-09-02', 15.58)
('MAPFRE', 'ENAGAS', '2022-09-02', 16.78)
('MAPFRE', 'FLUIDRA', '2022-09-02', 14.03)
('MAPFRE', 'FERROVIAL', '2022-09-02', 23.439999999999998)
('MAPFRE', 'GRIFOLS CL.A', '2022-09-02', 10.15)
('MAPFRE', 'IAG GROUP', '2022-09-02', 0.41999999999999993)
('MAPFRE', 'IBERDROLA', '2022-09-02', 8.89)
('MAPFRE', 'INDRA SISTEMAS', '2022-09-02', 6.09)
('MAPFRE', 'INDITEX', '2022-09-02', 20.03)
('MAPFRE', 'MELIA HOTELS', '2022-09-02', 4.28)
('MAPFRE', 'MERLIN PROP

('BANKINTER', 'SACYR VALLEHERMOSO', '2022-08-19', 2.6700000000000004)
('BANKINTER', 'SIEMENS GAMESA', '2022-08-19', 12.979999999999999)
('BANKINTER', 'SOLARIA ENERGIA Y MEDIO AMBIEN', '2022-08-19', 17.409999999999997)
('BANKINTER', 'TELEFONICA', '2022-08-19', 0.7400000000000002)
('CAIXABANK', 'ACS', '2022-08-19', 20.9)
('CAIXABANK', 'ACERINOX SA', '2022-08-19', 6.32)
('CAIXABANK', 'AENA', '2022-08-19', 123.07)
('CAIXABANK', 'AMADEUS', '2022-08-19', 53.0)
('CAIXABANK', 'ACCIONA', '2022-08-19', 204.02)
('CAIXABANK', 'CRP ACC ENER RN BR', '2022-08-19', 39.42)
('CAIXABANK', 'BANCO DE BILBAO VIZCAYA', '2022-08-19', 1.7200000000000002)
('CAIXABANK', 'BANKINTER', '2022-08-19', 2.0100000000000002)
('CAIXABANK', 'CELLNEX TELECOM', '2022-08-19', 39.550000000000004)
('CAIXABANK', 'INMOBILIARIA COLONIAL', '2022-08-19', 3.31)
('CAIXABANK', 'ENDESA', '2022-08-19', 15.18)
('CAIXABANK', 'ENAGAS', '2022-08-19', 16.43)
('CAIXABANK', 'FLUIDRA', '2022-08-19', 14.59)
('CAIXABANK', 'FERROVIAL', '2022-08-19'

...

('SOLARIA ENERGIA Y MEDIO AMBIEN', 'AMADEUS', '2021-12-10', 41.480000000000004)
('SOLARIA ENERGIA Y MEDIO AMBIEN', 'ACCIONA', '2021-12-10', 142.62)
('SOLARIA ENERGIA Y MEDIO AMBIEN', 'CRP ACC ENER RN BR', '2021-12-10', 14.690000000000001)
('SOLARIA ENERGIA Y MEDIO AMBIEN', 'BANCO DE BILBAO VIZCAYA', '2021-12-10', 10.969999999999999)
('SOLARIA ENERGIA Y MEDIO AMBIEN', 'BANKINTER', '2021-12-10', 11.77)
('SOLARIA ENERGIA Y MEDIO AMBIEN', 'CAIXABANK', '2021-12-10', 13.779999999999998)
('SOLARIA ENERGIA Y MEDIO AMBIEN', 'CELLNEX TELECOM', '2021-12-10', 36.4)
('SOLARIA ENERGIA Y MEDIO AMBIEN', 'INMOBILIARIA COLONIAL', '2021-12-10', 8.029999999999998)
('SOLARIA ENERGIA Y MEDIO AMBIEN', 'ENDESA', '2021-12-10', 3.5600000000000023)
('SOLARIA ENERGIA Y MEDIO AMBIEN', 'ENAGAS', '2021-12-10', 4.520000000000003)
('SOLARIA ENERGIA Y MEDIO AMBIEN', 'FLUIDRA', '2021-12-10', 16.67)
('SOLARIA ENERGIA Y MEDIO AMBIEN', 'FERROVIAL', '2021-12-10', 9.41)
('SOLARIA ENERGIA Y MEDIO AMBIEN', 'GRIFOLS CL.A', '202

('MERLIN PROPERTIES', 'ACS', '2021-11-26', 11.19)
('MERLIN PROPERTIES', 'ACERINOX SA', '2021-11-26', 0.27999999999999936)
('MERLIN PROPERTIES', 'AENA', '2021-11-26', 118.61999999999999)
('MERLIN PROPERTIES', 'AMADEUS', '2021-11-26', 46.910000000000004)
('MERLIN PROPERTIES', 'ACCIONA', '2021-11-26', 149.47)
('MERLIN PROPERTIES', 'CRP ACC ENER RN BR', '2021-11-26', 20.560000000000002)
('MERLIN PROPERTIES', 'BANCO DE BILBAO VIZCAYA', '2021-11-26', 4.98)
('MERLIN PROPERTIES', 'BANKINTER', '2021-11-26', 5.5200000000000005)
('MERLIN PROPERTIES', 'CAIXABANK', '2021-11-26', 7.54)
('MERLIN PROPERTIES', 'CELLNEX TELECOM', '2021-11-26', 42.910000000000004)
('MERLIN PROPERTIES', 'INMOBILIARIA COLONIAL', '2021-11-26', 1.67)
('MERLIN PROPERTIES', 'ENDESA', '2021-11-26', 10.249999999999998)
('MERLIN PROPERTIES', 'ENAGAS', '2021-11-26', 10.040000000000001)
('MERLIN PROPERTIES', 'FLUIDRA', '2021-11-26', 23.120000000000005)
('MERLIN PROPERTIES', 'FERROVIAL', '2021-11-26', 14.94)
('MERLIN PROPERTIES', 'G

('INMOBILIARIA COLONIAL', 'SOLARIA ENERGIA Y MEDIO AMBIEN', '2021-11-12', 7.780000000000001)
('INMOBILIARIA COLONIAL', 'TELEFONICA', '2021-11-12', 4.5200000000000005)
('ENDESA', 'ACS', '2021-11-12', 3.9800000000000004)
('ENDESA', 'ACERINOX SA', '2021-11-12', 8.139999999999999)
('ENDESA', 'AENA', '2021-11-12', 127.74999999999999)
('ENDESA', 'AMADEUS', '2021-11-12', 42.94)
('ENDESA', 'ACCIONA', '2021-11-12', 140.3)
('ENDESA', 'CRP ACC ENER RN BR', '2021-11-12', 11.760000000000002)
('ENDESA', 'BANCO DE BILBAO VIZCAYA', '2021-11-12', 13.07)
('ENDESA', 'BANKINTER', '2021-11-12', 14.219999999999999)
('ENDESA', 'CAIXABANK', '2021-11-12', 16.7)
('ENDESA', 'CELLNEX TELECOM', '2021-11-12', 35.16)
('ENDESA', 'INMOBILIARIA COLONIAL', '2021-11-12', 10.719999999999999)
('ENDESA', 'ENAGAS', '2021-11-12', 0.7300000000000004)
('ENDESA', 'FLUIDRA', '2021-11-12', 14.45)
('ENDESA', 'FERROVIAL', '2021-11-12', 7.150000000000002)
('ENDESA', 'GRIFOLS CL.A', '2021-11-12', 0.9399999999999977)
('ENDESA', 'IAG GR

('ACS', 'AENA', '2021-10-29', 119.02000000000001)
('ACS', 'AMADEUS', '2021-10-29', 35.21000000000001)
('ACS', 'ACCIONA', '2021-10-29', 143.17000000000002)
('ACS', 'CRP ACC ENER RN BR', '2021-10-29', 7.600000000000001)
('ACS', 'BANCO DE BILBAO VIZCAYA', '2021-10-29', 16.57)
('ACS', 'BANKINTER', '2021-10-29', 17.869999999999997)
('ACS', 'CAIXABANK', '2021-10-29', 20.14)
('ACS', 'CELLNEX TELECOM', '2021-10-29', 30.55)
('ACS', 'INMOBILIARIA COLONIAL', '2021-10-29', 14.219999999999999)
('ACS', 'ENDESA', '2021-10-29', 2.6799999999999997)
('ACS', 'ENAGAS', '2021-10-29', 3.219999999999999)
('ACS', 'FLUIDRA', '2021-10-29', 10.419999999999998)
('ACS', 'FERROVIAL', '2021-10-29', 4.630000000000003)
('ACS', 'GRIFOLS CL.A', '2021-10-29', 2.8299999999999983)
('ACS', 'IAG GROUP', '2021-10-29', 20.7)
('ACS', 'IBERDROLA', '2021-10-29', 12.409999999999998)
('ACS', 'INDRA SISTEMAS', '2021-10-29', 12.18)
('ACS', 'INDITEX', '2021-10-29', 8.61)
('ACS', 'MAPFRE', '2021-10-29', 20.799999999999997)
('ACS', 'MEL

('MERLIN PROPERTIES', 'BANCO SANTANDER', '2021-10-22', 6.07)
('MERLIN PROPERTIES', 'SACYR VALLEHERMOSO', '2021-10-22', 6.92)
('MERLIN PROPERTIES', 'SIEMENS GAMESA', '2021-10-22', 12.570000000000002)
('MERLIN PROPERTIES', 'SOLARIA ENERGIA Y MEDIO AMBIEN', '2021-10-22', 7.610000000000001)
('MERLIN PROPERTIES', 'TELEFONICA', '2021-10-22', 5.58)
('ARCELORMITTAL', 'ACS', '2021-10-22', 4.16)
('ARCELORMITTAL', 'ACERINOX SA', '2021-10-22', 15.629999999999999)
('ARCELORMITTAL', 'AENA', '2021-10-22', 114.72999999999999)
('ARCELORMITTAL', 'AMADEUS', '2021-10-22', 28.18)
('ARCELORMITTAL', 'ACCIONA', '2021-10-22', 133.88)
('ARCELORMITTAL', 'CRP ACC ENER RN BR', '2021-10-22', 2.740000000000002)
('ARCELORMITTAL', 'BANCO DE BILBAO VIZCAYA', '2021-10-22', 21.529999999999998)
('ARCELORMITTAL', 'BANKINTER', '2021-10-22', 22.5)
('ARCELORMITTAL', 'CAIXABANK', '2021-10-22', 24.68)
('ARCELORMITTAL', 'CELLNEX TELECOM', '2021-10-22', 27.4)
('ARCELORMITTAL', 'INMOBILIARIA COLONIAL', '2021-10-22', 18.9)
('ARCELO

In [9]:
import sqlite3

conn=sqlite3.connect("Bolsa.sqlite3")
conn.execute("PRAGMA foreign_keys = 1")
cur=conn.cursor()

#Consulta 7:
#¿En que fecha de la serie histórica del IBEX35 hubo más acciones donde la diferencia entre el valor maximo 
#y el precio final fue 0? Mostrar los nombres de las acciones y la fecha.
cur.execute(
"SELECT dg.Nombre," +
"       si.Fecha" +
"  FROM SemanalesIBEX35 si" +
"       JOIN" +
"       DatosGenerales dg USING (" +
"           Ticker" +
"       )" +
" WHERE Fecha == (" +
"                    SELECT Fecha" +
"                      FROM (" +
"                               SELECT Fecha," +
"                                      MAX(res.count) " +
"                                 FROM (" +
"                                          SELECT COUNT( * ) AS count," +
"                                                 Ticker," +
"                                                 Fecha" +
"                                            FROM SemanalesIBEX35" +
"                                           WHERE High == Price" +
"                                           GROUP BY Fecha" +
"                                      )" +
"                                      AS res" +
"                           )" +
"                )" +
"AND " +
"       High == Price;"

)

mostrar(cur)

cur.close()
conn.commit()

('AENA', '2022-01-14')
('CAIXABANK', '2022-01-14')
('ENAGAS', '2022-01-14')
('MAPFRE', '2022-01-14')
('BANCO SANTANDER', '2022-01-14')
